# Pose Detection with OpenPose

This notebook uses an open source project [CMU-Perceptual-Computing-Lab/openpose](https://github.com/CMU-Perceptual-Computing-Lab/openpose.git) to detect/track multi person poses on a given youtube video.

For other deep-learning Colab notebooks, visit [tugstugi/dl-colab-notebooks](https://github.com/tugstugi/dl-colab-notebooks).


## Install OpenPose
#### (This will take some time)

In [ ]:
import os
from os.path import exists, join, basename, splitext

git_repo_url = 'https://github.com/CMU-Perceptual-Computing-Lab/openpose.git'
project_name = splitext(basename(git_repo_url))[0]
if not exists(project_name):
  # see: https://github.com/CMU-Perceptual-Computing-Lab/openpose/issues/949
  # install new CMake becaue of CUDA10
  !wget -q https://cmake.org/files/v3.13/cmake-3.13.0-Linux-x86_64.tar.gz
  !tar xfz cmake-3.13.0-Linux-x86_64.tar.gz --strip-components=1 -C /usr/local
  # clone openpose
  !git clone -q --depth 1 $git_repo_url
  !sed -i 's/execute_process(COMMAND git checkout master WORKING_DIRECTORY ${CMAKE_SOURCE_DIR}\/3rdparty\/caffe)/execute_process(COMMAND git checkout f019d0dfe86f49d1140961f8c7dec22130c83154 WORKING_DIRECTORY ${CMAKE_SOURCE_DIR}\/3rdparty\/caffe)/g' openpose/CMakeLists.txt
  # install system dependencies
  !apt-get -qq install -y libatlas-base-dev libprotobuf-dev libleveldb-dev libsnappy-dev libhdf5-serial-dev protobuf-compiler libgflags-dev libgoogle-glog-dev liblmdb-dev opencl-headers ocl-icd-opencl-dev libviennacl-dev
  # install python dependencies
  !pip install -q youtube-dl
  # build openpose
  !cd openpose && rm -rf build || true && mkdir build && cd build && cmake .. && make -j`nproc`

Selecting previously unselected package libgflags2.2.
(Reading database ... 160980 files and directories currently installed.)
Preparing to unpack .../00-libgflags2.2_2.2.1-1_amd64.deb ...
Unpacking libgflags2.2 (2.2.1-1) ...
Selecting previously unselected package libgflags-dev.
Preparing to unpack .../01-libgflags-dev_2.2.1-1_amd64.deb ...
Unpacking libgflags-dev (2.2.1-1) ...
Selecting previously unselected package libgoogle-glog0v5.
Preparing to unpack .../02-libgoogle-glog0v5_0.3.5-1_amd64.deb ...
Unpacking libgoogle-glog0v5 (0.3.5-1) ...
Selecting previously unselected package libgoogle-glog-dev.
Preparing to unpack .../03-libgoogle-glog-dev_0.3.5-1_amd64.deb ...
Unpacking libgoogle-glog-dev (0.3.5-1) ...
Selecting previously unselected package libhdf5-serial-dev.
Preparing to unpack .../04-libhdf5-serial-dev_1.10.0-patch1+docs-4_all.deb ...
Unpacking libhdf5-serial-dev (1.10.0-patch1+docs-4) ...
Selecting previously unselected package libleveldb1v5:amd64.
Preparing to unpack ...

In [ ]:
ls

cmake-3.13.0-Linux-x86_64.tar.gz  openpose/  sample_data/


## Detect poses on a video uploaded to Drive
#### <b>NOTE:</b> In the team project google drive there is a folder called 'Videos'; make a copy and place that in your personal drive root directory (My Drive) before running this code
We will detect poses in the following video:

In [ ]:
# Mount drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# Display selected video
from IPython.core.display import Video
video_path = '/content/drive/MyDrive/Videos'
nba_path = join(video_path, 'nba')
novice_path = join(video_path, 'novice')

# define paths to all videos (1-10)
# NBA
dame = []
for i in range(11):
  dame.append(join(nba_path, 'dame', 'dame_' + str(i) + '.mp4'))
kat = []
for i in range(11):
  kat.append(join(nba_path, 'kat', 'kat_' + str(i) + '.mp4'))
steph = []
for i in range(11):
  steph.append(join(nba_path, 'steph', 'steph_' + str(i) + '.mp4'))
# NOVICE
alex = []
for i in range(11):
  alex.append(join(novice_path, 'alex', 'alex_' + str(i) + '.mp4'))
alex.append(join(novice_path, 'alex', 'money.mp4'))
chris = []
for i in range(11):
  chris.append(join(novice_path, 'chris', 'chris_' + str(i) + '.mp4'))
chris.append(join(novice_path, 'chris', 'money.mp4'))
thomas = []
for i in range(11):
  thomas.append(join(novice_path, 'thomas', 'thomas_' + str(i) + '.mp4'))
thomas.append(join(novice_path, 'thomas', 'money.mp4'))

# path to video currently analyzing (1-10)
name = 'chris'                                      # SELECT SHOOTER NAME HERE
num = 11                                            # SELECT SHOT NUMBER HERE (1-10)... BONUS 11 (money)
video_path = chris[num]                             # SELECT LIST CORRESPONDING TO SHOOTER NAME HERE

video = Video(video_path, embed=True)
video

Output hidden; open in https://colab.research.google.com to view.

Perform pose detection on the video (no trimming necessary)

In [ ]:
# detect poses on the these 5 seconds
!rm openpose.avi
!cd openpose && ./build/examples/openpose/openpose.bin --video ../../{video_path} --write_json ./output/ --display 0  --write_video ../openpose.avi --hand
# convert the result into MP4
!ffmpeg -y -loglevel info -i openpose.avi output.mp4

In [ ]:
%ls

cmake-3.13.0-Linux-x86_64.tar.gz  openpose/     output.mp4    video.mp4
drive/                            openpose.avi  sample_data/  youtube.mp4


Finally, visualize the result:

In [ ]:
def show_local_mp4_video(file_name, width=640, height=480):
  import io
  import base64
  from IPython.display import HTML
  video_encoded = base64.b64encode(io.open(file_name, 'rb').read())
  return HTML(data='''<video width="{0}" height="{1}" alt="test" controls>
                        <source src="data:video/mp4;base64,{2}" type="video/mp4" />
                      </video>'''.format(width, height, video_encoded.decode('ascii')))

show_local_mp4_video('output.mp4', width=960, height=720)

Output hidden; open in https://colab.research.google.com to view.

Download outputs

In [ ]:
# from google.colab import files
# zip_name = name + str(num)
# !zip -r ./openpose/{zip_name}.zip ./openpose/output
# files.download("./openpose/" + zip_name + ".zip")

updating: openpose/output/ (stored 0%)
updating: openpose/output/money_000000000141_keypoints.json (deflated 58%)
updating: openpose/output/money_000000000036_keypoints.json (deflated 57%)
updating: openpose/output/money_000000000082_keypoints.json (deflated 58%)
updating: openpose/output/chris_1_000000000033_keypoints.json (deflated 58%)
updating: openpose/output/video_000000000107_keypoints.json (deflated 58%)
updating: openpose/output/money_000000000071_keypoints.json (deflated 57%)
updating: openpose/output/money_000000000117_keypoints.json (deflated 58%)
updating: openpose/output/money_000000000123_keypoints.json (deflated 58%)
updating: openpose/output/money_000000000080_keypoints.json (deflated 57%)
updating: openpose/output/video_000000000065_keypoints.json (deflated 60%)
updating: openpose/output/money_000000000143_keypoints.json (deflated 58%)
updating: openpose/output/money_000000000011_keypoints.json (deflated 57%)
updating: openpose/output/money_000000000032_keypoints.json

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
from google.colab import files

def OpenPoseAnalysis(video_path, name, num):
  # detect poses on the these 5 seconds
  !rm openpose.avi
  !cd openpose && ./build/examples/openpose/openpose.bin --video ../../{video_path} --write_json ./output/ --display 0  --write_video ../openpose.avi
  # convert the result into MP4
  !ffmpeg -y -i openpose.avi output.mp4
  # download zip
  zip_name = name + str(num)
  !zip -r ./openpose/{zip_name}.zip ./openpose/output

# loop to analyze and download all videos
for i in range(1,11):       
  video_path = dame[i]  
  OpenPoseAnalysis(video_path, 'dame', i)
for i in range(1,11):       
  video_path = kat[i]  
  OpenPoseAnalysis(video_path, 'kat', i)
for i in range(1,11):       
  video_path = steph[i]  
  OpenPoseAnalysis(video_path, 'steph', i)
for i in range(1,11):       
  video_path = alex[i]  
  OpenPoseAnalysis(video_path, 'alex', i)
for i in range(1,11):       
  video_path = chris[i]  
  OpenPoseAnalysis(video_path, 'chris', i)
for i in range(1,11):       
  video_path = thomas[i]  
  OpenPoseAnalysis(video_path, 'thomas', i)

files.download("./openpose/" + "thomas10" + ".zip")

rm: cannot remove 'openpose.avi': No such file or directory
Starting OpenPose demo...
Configuring OpenPose...
Starting thread(s)...
Auto-detecting all available GPUs... Detected 1 GPU(s), using 1 of them starting at GPU 0.
^C
ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Starting OpenPose demo...
Configuring OpenPose...
Starting thread(s)...
Auto-detecting all available GPUs... Detected 1 GPU(s), using 1 of them starting at GPU 0.
OpenPose demo successfully finished. Total time: 8.201568 seconds.
ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsn

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Starting OpenPose demo...
Configuring OpenPose...
Starting thread(s)...
Auto-detecting all available GPUs... Detected 1 GPU(s), using 1 of them starting at GPU 0.
OpenPose demo successfully finished. Total time: 6.712780 seconds.
ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsn

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>